<a href="https://colab.research.google.com/github/kartthik-18/Lane-Detection-With-OpenCV-Project/blob/main/Lane_Detection_With_OpenCV_Project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import files
uploaded = files.upload()

Saving trialvideo.mp4 to trialvideo (1).mp4


In [ ]:
import cv2
import numpy as np
from google.colab.patches import cv2_imshow  # Use this instead of cv2.imshow()

def make_coordinates(image, line):
    slope, intercept = line
    y1 = int(image.shape[0])
    y2 = int(y1 * (3/5))
    x1 = int((y1 - intercept) / slope)
    x2 = int((y2 - intercept) / slope)
    return [[x1, y1, x2, y2]]

def average_slope_intercept(image, lines):
    left_fitting = []
    right_fitting = []

    if lines is None:
        return None

    for line in lines:
        x1, y1, x2, y2 = line.reshape(4)
        parameters = np.polyfit((x1, x2), (y1, y2), 1)
        slope = parameters[0]
        intercept = parameters[1]
        if slope < 0:
            left_fitting.append((slope, intercept))
        else:
            right_fitting.append((slope, intercept))

    if len(left_fitting) == 0 or len(right_fitting) == 0:
        return None

    left_fitting_average = np.average(left_fitting, axis=0)
    right_fitting_average = np.average(right_fitting, axis=0)

    left_line = make_coordinates(image, left_fitting_average)
    right_line = make_coordinates(image, right_fitting_average)

    return np.array([left_line, right_line])

def canny_func(image):
    gray = cv2.cvtColor(image, cv2.COLOR_RGB2GRAY)
    kernel = 5
    blur = cv2.GaussianBlur(gray, (kernel, kernel), 0)
    canny = cv2.Canny(blur, 50, 150)
    return canny

def display_lines(image, lines):
    line_image = np.zeros_like(image)
    if lines is not None:
        for line in lines:
            for x1, y1, x2, y2 in line:
                cv2.line(line_image, (x1, y1), (x2, y2), (255, 0, 0), 10)
    return line_image

def region_of_interest(canny):
    height = canny.shape[0]
    width = canny.shape[1]
    mask = np.zeros_like(canny)
    triangle = np.array([[
        (200, height),
        (550, 250),
        (1100, height),
    ]], np.int32)
    cv2.fillPoly(mask, triangle, 255)
    masked_image = cv2.bitwise_and(canny, mask)
    return masked_image

captureframes = cv2.VideoCapture("trialvideo.mp4")

width = int(captureframes.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(captureframes.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps = captureframes.get(cv2.CAP_PROP_FPS)
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
output = cv2.VideoWriter('output_video.mp4', fourcc, fps, (width, height))

while captureframes.isOpened():
    ret, frame = captureframes.read()
    if not ret:
        break

    canny_image = canny_func(frame)
    cropped_canny = region_of_interest(canny_image)
    lines = cv2.HoughLinesP(cropped_canny, 2, np.pi/180, 100, np.array([]), minLineLength=40, maxLineGap=5)

    averaged_lines = average_slope_intercept(frame, lines)
    line_image = display_lines(frame, averaged_lines)
    combo_image = cv2.addWeighted(frame, 0.8, line_image, 1, 1)

    output.write(combo_image)  # Save frame to video

captureframes.release()
output.release()
cv2.destroyAllWindows()



In [ ]:
# Install ffmpeg if not already installed
!apt-get install -y ffmpeg

# Convert video for compatibility using libx264 codec
!ffmpeg -i output_video.mp4 -vcodec libx264 output_clean.mp4 -y

# Display the converted video inside Colab
from IPython.display import Video
Video("output_clean.mp4", embed=True, width=600)


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
0 upgraded, 0 newly installed, 0 to remove and 35 not upgraded.
ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq -

In [ ]:
from google.colab import files
files.download('output_video.mp4')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>